In [ ]:
pwd

In [8]:
import gensim
import re
from bs4 import BeautifulSoup
import csv
import numpy as np
import pandas as pd

In [9]:
def load(file_name):
    with open(file_name, 'r', encoding="utf8") as myfile:
        return BeautifulSoup(myfile.read(), "xml")
    
    
def remove_subject_from_question(question):
    a =  re.sub('.+\/\/\ ', '', question);
    # UWAGA na komentarze
    if (a != question):
        print(question + " " + a + "\n")
    return a

def load_dataset_subject_and_body(xml_file):
    print("Loading dataset - subject and body...")
    
    soup = load(xml_file)
    original_questions = soup.findAll("OrgQuestion")
    dataset = []
    
    for original_question in original_questions:
        related_questions = original_question.findAll("RelQuestion")
        
        for related_question in related_questions:
            
#             original_question_text = original_question.OrgQSubject.text + ". " + 
            original_question_text = original_question.OrgQBody.text
            related_question_text = related_question.RelQBody.text
#             related_question_text = related_question.RelQSubject.text + ". " + related_question.RelQBody.text
            
            dataset_sample = dict([("question1", original_question_text),
                                    ("question1_id", original_question['ORGQ_ID']),
                                    ("question2", related_question_text),
                                    ("question2_id", related_question['RELQ_ID']),
                                    ("relevance", related_question['RELQ_RELEVANCE2ORGQ'])])
            
            dataset.append(dataset_sample)
            
    print("Finished loading dataset")

    return dataset    
    
def load_dataset_subject(xml_file):
    print("Loading dataset - only subject")
    
def load_dataset_body(xml_file):
    print("Loading dataset - only body")
    
def label_to_class_2(label):
    if label == "Irrelevant":
        return 0
    else:
        return 1

In [10]:
# prepare test file csv as well as proper train_p1, train_p2 oraz dev sets

def load_and_save_dataset_subject_and_body(xml_file, output_file, test=False):
    print("Loading dataset - subject and body...")
    
    soup = load(xml_file)
    original_questions = soup.findAll("OrgQuestion")
    dataset = []
    
    for original_question in original_questions:
        related_questions = original_question.findAll("RelQuestion")
        
        for related_question in related_questions:
            
            original_question_text = original_question.OrgQBody.text
            related_question_text = related_question.RelQBody.text
            
            if test:
                dataset_sample = dict([("question1", original_question_text),
                                    ("question1_id", original_question['ORGQ_ID']),
                                    ("question2", related_question_text),
                                    ("question2_id", related_question['RELQ_ID'])])
            else:
                dataset_sample = dict([("question1", original_question_text),
                                    ("question1_id", original_question['ORGQ_ID']),
                                    ("question2", related_question_text),
                                    ("question2_id", related_question['RELQ_ID']),
                                    ("relevance", related_question['RELQ_RELEVANCE2ORGQ'])])
                        
            dataset.append(dataset_sample)
            
    print("Finished loading dataset")
    
    print("Saving dataset")
    
    with open(output_file, 'w', newline='') as csvfile:
    

        writer = csv.writer(csvfile, delimiter=',', quotechar='|', quoting=csv.QUOTE_MINIMAL)
        writer.writerow(['id', 'question1_id', 'question2_id', 'question1', 'question2', 'relevance'])

        for i, elem in enumerate(dataset):
            print(i, elem)
            if test:
                writer.writerow([i, elem['question1_id'], elem['question2_id'], elem['question1'], elem['question2']])
            else:
                writer.writerow([i, elem['question1_id'], elem['question2_id'], elem['question1'], elem['question2'], elem['relevance']])  



train_p1_file = "../data/SemEval2016-Task3-CQA-QL-train-part1.xml"
train_p2_file = "../data/SemEval2016-Task3-CQA-QL-train-part2.xml"
dev_file = "../data/SemEval2016-Task3-CQA-QL-dev.xml"
# test_file =  "../data/SemEval2017-task3-English-test-input.xml"

out_train_p1_file = "augmented/train_part1.csv"
out_train_p2_file = "augmented/train_part2.csv"
out_dev_file = "augmented/dev.csv"
# out_test_file =  "augmented/test.csv"


load_and_save_dataset_subject_and_body(train_p1_file, out_train_p1_file) 
load_and_save_dataset_subject_and_body(train_p2_file, out_train_p2_file) 
load_and_save_dataset_subject_and_body(dev_file, out_dev_file) 
# load_and_save_dataset_subject_and_body(test_file, out_test_file, True) 

# output_file = "subtask_B_train_and_dev_dataset.csv"



Loading dataset - subject and body...
Finished loading dataset
Saving dataset
0 {'question1': 'Where I can buy good oil for massage?', 'question1_id': 'Q1', 'question2': 'is there any place i can find scented massage oils in qatar?', 'question2_id': 'Q1_R1', 'relevance': 'PerfectMatch'}
1 {'question1': 'Where I can buy good oil for massage?', 'question1_id': 'Q1', 'question2': 'Hi;Can any one tell me a place where i can have a good massage drom philipinies????? yesterday i had a massage in Bio-Bil they charged me 300qr for 01 hour bt it is totally waste... pls advice me if theres any philipinos....', 'question2_id': 'Q1_R6', 'relevance': 'Relevant'}
2 {'question1': 'Where I can buy good oil for massage?', 'question1_id': 'Q1', 'question2': "Tell me; where is the best place to go for a massage? Mind you; I don't want to spend 1000QR for it... (Guys; please don't come up with answers that you\xa0would gladly do it yourself; plz...)\xa0", 'question2_id': 'Q1_R8', 'relevance': 'Irrelevant'

303 {'question1': 'Before everyone shouts at me - I did a search and the info seems to be a bit old.(2006-2007) So at the risk of being ridiculed - can I just ask a simple question? Can I rent a car with an international driving license while waiting for my residency permit? Even if I have been here longer than 7 days? Its all very confusing!', 'question1_id': 'Q31', 'question2': "my kids have just got their next karate belt; and we promised them a 'slap-up' sushi meal to celebrate. Is there a proper sushi bar in Doha; apart from the hotels? all suggestions welcomed; on behalf of an 8 & 10 year old... thanks; Grantley", 'question2_id': 'Q31_R23', 'relevance': 'Irrelevant'}
304 {'question1': 'Before everyone shouts at me - I did a search and the info seems to be a bit old.(2006-2007) So at the risk of being ridiculed - can I just ask a simple question? Can I rent a car with an international driving license while waiting for my residency permit? Even if I have been here longer than 7 day

1038 {'question1': 'Can anyone tell me when camel races are held? Thank you.', 'question1_id': 'Q104', 'question2': 'Has anyone been caught drink driving here? I got caught last week; just wondering what penalty i can expect. Hoping for just a fine but wondering if anyone has had worse punishment. Also can you leave the cuntry (spelt on purpose by the way!) whilst still awaiting ur trial? Cheers.', 'question2_id': 'Q104_R67', 'relevance': 'Irrelevant'}
1039 {'question1': 'Can anyone tell me when camel races are held? Thank you.', 'question1_id': 'Q104', 'question2': 'i\xa0 just think that what if we will make a QL Cricket Team... anyone intrested...? Mind It I will be the Captain Of The Team...lolz..[Joke]', 'question2_id': 'Q104_R77', 'relevance': 'Irrelevant'}
1040 {'question1': 'hi.. I have come to qatar in visit visa.and i like to work in qatar.but i heard that girls with visit visa cant seek jobs here.i would like to know is it possible for me to work here under these limitations.

1589 {'question1': 'If any body know about any car less than 1000 riyal for rental;please answer me.', 'question1_id': 'Q159', 'question2': "I'm looking for XBOX 360. Anyone knows where I can find it in Doha? I could not find it Hyatt Plaza; does anyone know of some other place that sells it? ...and how much it costs?", 'question2_id': 'Q159_R45', 'relevance': 'Irrelevant'}
1590 {'question1': 'Hi; My husband will start work in Qatar soon and we were wondering how is the work pace there? is it typical regular hours ( 9 to 5) or does it involve much of overtime/ weekend work/ Anyone with insides from the financial sector would be very helpful ;-) Thanks. (sorry as I initially posted my question in the wrong place)', 'question1_id': 'Q160', 'question2': "Sorry for the girly nature of this question; but I'm desperate. Ladies; can you recommend a decent hairdresser in Doha? I've been here several months and all I've heard are horror stories. Any suggestions would be gratefully received; my 

259 {'question1': 'I moved to Doha three months back. I want to know from where can i drink alochol in cheap rates. I went to ramada; W; they are very expensive. Secondly i want to know what if i am drunk and coming out from bar and going to my room. Means is there any problem for me as i am a muslim guy. I shall be very thankful if someone posts the suitable answer.', 'question1_id': 'Q226', 'question2': 'I just want to share my opinion on a couple of the clubs in Doha; Ritz carlton is quite nice with the nicest pool in Doha. Recommended. Diplomatic Club has now banned bikinis and are giving warning letters for using bikinis in the pool! Apparently all the western expats have left and it is now an arabic club. Other views?', 'question2_id': 'Q226_R60', 'relevance': 'Irrelevant'}
260 {'question1': 'Could anyone please advise me; I have just been offered a position in a construction company in Qatar and I was wondering if you can buy alcohol from shops and bars or is it restricted like 

624 {'question1': "Hello! We will be soon relocated to Doha. In sight of the living costs (rent; etc.) a friend and I have decided to share a flat or villa whilst in Doha. Can you guys please tell us if this can be done? if it's okay in Doha? if you have heard of other people doing the same? Your input is appreciated. Regards;", 'question1_id': 'Q263', 'question2': 'A friend of mine asked me to post this question His girlfriend is coming to visit him from the US and they wanna stay at a hotel; would it be ok for them to take a hotel room?', 'question2_id': 'Q263_R9', 'relevance': 'Relevant'}
625 {'question1': "Hello! We will be soon relocated to Doha. In sight of the living costs (rent; etc.) a friend and I have decided to share a flat or villa whilst in Doha. Can you guys please tell us if this can be done? if it's okay in Doha? if you have heard of other people doing the same? Your input is appreciated. Regards;", 'question1_id': 'Q263', 'question2': "Hi Everyone; I'm currently negot

310 {'question1': 'What do you think of it?', 'question1_id': 'Q299', 'question2': 'hmm?', 'question2_id': 'Q299_R4', 'relevance': 'PerfectMatch'}
311 {'question1': 'What do you think of it?', 'question1_id': 'Q299', 'question2': 'I had a one night stand with someone from a bar (yeah I know its not right...)... I coudnt stop thinking about him...What should I do???', 'question2_id': 'Q299_R5', 'relevance': 'PerfectMatch'}
312 {'question1': 'What do you think of it?', 'question1_id': 'Q299', 'question2': 'how to mend a broken sweet heart????', 'question2_id': 'Q299_R6', 'relevance': 'Irrelevant'}
313 {'question1': 'What do you think of it?', 'question1_id': 'Q299', 'question2': "On this weekend ; I am planning to go to some bar.Had'nt any drink for 5 weeks.Can some one give rating on the bars; Criteria; drinks and ambiance?", 'question2_id': 'Q299_R8', 'relevance': 'Irrelevant'}
314 {'question1': 'What do you think of it?', 'question1_id': 'Q299', 'question2': 'This was a new one to me.

'/Users/jacek/projects/cqa-sem-eval/subtask_B'

In [12]:
# export original data to csv

input_files = [
    "../data/SemEval2016-Task3-CQA-QL-train-part1.xml",
    "../data/SemEval2016-Task3-CQA-QL-train-part2.xml",
    "../data/SemEval2016-Task3-CQA-QL-dev.xml"
]

output_file = "augmented/subtask_B_train_and_dev_dataset.csv"

with open(output_file, 'w', newline='') as csvfile:
    
    dataset = []
    for file in input_files:
        dataset.append(load_dataset_subject_and_body(file))
        
    writer = csv.writer(csvfile, delimiter=',', quotechar='|', quoting=csv.QUOTE_MINIMAL)
    writer.writerow(['id', 'question1_id', 'question2_id', 'question1', 'question2', 'relevance'])
    
    for i, elem in enumerate(np.concatenate(dataset)):
        print(i, elem)
        writer.writerow([i, elem['question1_id'], elem['question2_id'], elem['question1'], elem['question2'], elem['relevance']])


Loading dataset - subject and body...
Finished loading dataset
Loading dataset - subject and body...
Finished loading dataset
Loading dataset - subject and body...
Finished loading dataset
0 {'question1': 'Where I can buy good oil for massage?', 'question1_id': 'Q1', 'question2': 'is there any place i can find scented massage oils in qatar?', 'question2_id': 'Q1_R1', 'relevance': 'PerfectMatch'}
1 {'question1': 'Where I can buy good oil for massage?', 'question1_id': 'Q1', 'question2': 'Hi;Can any one tell me a place where i can have a good massage drom philipinies????? yesterday i had a massage in Bio-Bil they charged me 300qr for 01 hour bt it is totally waste... pls advice me if theres any philipinos....', 'question2_id': 'Q1_R6', 'relevance': 'Relevant'}
2 {'question1': 'Where I can buy good oil for massage?', 'question1_id': 'Q1', 'question2': "Tell me; where is the best place to go for a massage? Mind you; I don't want to spend 1000QR for it... (Guys; please don't come up with an

409 {'question1': 'How many days does it take to have Family Visit Visa ? Is that the most quick way to bring my wife to doha? Even she is canceled ; can she work again after i bring her with my sponsorship (as my wife)?? Thanks aLL', 'question1_id': 'Q41', 'question2': "Hi all need your help/advice we'll be in Qatar next week; me on a working visa and tourist visa for my family (wife son;daughter). My query is can I convert their tourist visa to family visit visa even I dont have yet a Qatar ID? My profession in visa is Civil Engineer. Thanks in advance..", 'question2_id': 'Q41_R56', 'relevance': 'Relevant'}
410 {'question1': "Hi guys I just got a parking ticket :( Does anyone know how much I'll have to pay? Can't get into moi.gov.qa at the moment. thanks", 'question1_id': 'Q42', 'question2': 'Hello QLers; Recently one of my colleague paid 6000 QAR for red light crossing. Which is his one month salary approx. I heard from many that on an average Traffic violation fine is around 1000 Q

1027 {'question1': 'Many clinics : but which one is good and provides a reliable professional service at sensible prices ?', 'question1_id': 'Q103', 'question2': 'Hi; Any doctors around working at HMC as resident? I have applied for residency training program at HMC. Awaiting reply; however; I was wondring what would be the salary to expect and allownaces? Do they offer accommodation to married couples? If not what kind of living allowance they give? Basic salary? How is the training there at HMC? Your guidance will be appreciated. Thanks. S.', 'question2_id': 'Q103_R48', 'relevance': 'Irrelevant'}
1028 {'question1': 'Many clinics : but which one is good and provides a reliable professional service at sensible prices ?', 'question1_id': 'Q103', 'question2': "Can anyone recommend a good female dentist? I haven't been to a dentist yet in Qatar and am a bit worried! Phone numbers and references appreciated!", 'question2_id': 'Q103_R49', 'relevance': 'PerfectMatch'}
1029 {'question1': 'Man

1773 {'question1': 'Is there anyway to avoid the requirement of a NOC if you want to change a job and your employer does not want to give you a NOC?', 'question1_id': 'Q178', 'question2': 'Bharain No need NOC; Qatar when???', 'question2_id': 'Q178_R32', 'relevance': 'Relevant'}
1774 {'question1': 'Is there anyway to avoid the requirement of a NOC if you want to change a job and your employer does not want to give you a NOC?', 'question1_id': 'Q178', 'question2': 'Hi there I am hoping to take up an offer of employment soon in Qatar. My question is...i currently have a personal loan in the UAE;and will not be able to leave the UAE; before it is settled. Is there anyway I can obtain a personal loan in Qatar before I leave the UAE; so that i can settle my finances her before I leave? Any advise from anyone in a similar situation? Thanks', 'question2_id': 'Q178_R36', 'relevance': 'Irrelevant'}
1775 {'question1': 'Is there anyway to avoid the requirement of a NOC if you want to change a job 

2490 {'question1': 'Recently I heard that QCB has instructed to reduce the loan interest to 6 % for the new and existing loan holders. Any update on this I am HSBC customer and still they deduct same amount... Any info from when this will effect and it is mandatory to all the Banks ( As i heard from my friend QNB already confirm they reduce the interest therefore loan repayment period has reduce) What a relief if this true????', 'question1_id': 'Q250', 'question2': "HI; I'm moving to Doha in April and I've been trying to research what the current Interest rates are for Vehicle and Personal loans as I will more than likely be needing a loan for a car whilst I am out there. I've managed to find the Commercial bank rate and QNB rate but I cant seem to find HSBC. Does anyone know what it is please? I'm looking at borrowing between 60;000 - 100;000 QR thanks", 'question2_id': 'Q250_R3', 'relevance': 'Irrelevant'}
2491 {'question1': 'Recently I heard that QCB has instructed to reduce the loa

In [13]:
# export extended data

# dataset = np.concatenate(dataset)

result = {}

with open(output_file, 'r') as csvfile:
    csvreader = csv.reader(csvfile, delimiter=',', quotechar='"')
    next(csvreader, None)

    for row in csvreader:
        if row[1] in result:
            result[row[1]].append(row)
        else:
            result[row[1]] = [row]
            
        

In [19]:
len(result)

317

In [23]:
total_extra_pairs = []

for i, key in enumerate(result.keys()):
    batch = result[key]
    perfect_matches = [item for item in batch if item[5] == 'Irrelevant']
        
#     print(i, batch[0][1], len(perfect_matches))

    extra_pairs = []
    matches_size = len(perfect_matches)
    
    for perfect_elem_idx, perfect_el in enumerate(perfect_matches):
#         print(perfect_elem_idx)
        
        for iii, element in enumerate(perfect_matches[perfect_elem_idx+1:matches_size]):
#             print(iii)
            extra_pairs.append([perfect_el[2], element[2], perfect_el[4], element[4], "Irrelevant"])
    
    if len(extra_pairs) > 0:
        total_extra_pairs.append(extra_pairs)
    
with open("augmented/generated_irrelevant.csv", 'w') as csvfile:
    print(csvfile)
    writer = csv.writer(csvfile, delimiter=',', quotechar='|', quoting=csv.QUOTE_MINIMAL)
    writer.writerow(['id', 'question1_id', 'question2_id', 'question1', 'question2', 'relevance'])
    
    for i, elem in enumerate(np.concatenate(total_extra_pairs)):
#         print(i, elem)
        writer.writerow([i, elem[0], elem[1], elem[2], elem[3], elem[4]])
    

<_io.TextIOWrapper name='augmented/generated_irrelevant.csv' mode='w' encoding='UTF-8'>


In [24]:
def generate_extra_question_pairs(target_output_file="augmented/newly_generated.csv"):
    total_extra_pairs = []
    
    for relevance in ["PerfectMatch", "Relevant", "Irrelevant"]:

        for i, key in enumerate(result.keys()):
            batch = result[key]
            perfect_matches = [item for item in batch if item[5] == relevance]

            print(i, batch[0][1], len(perfect_matches))

            extra_pairs = []
            matches_size = len(perfect_matches)

            for perfect_elem_idx, perfect_el in enumerate(perfect_matches):
                print(perfect_elem_idx)

                for iii, element in enumerate(perfect_matches[perfect_elem_idx+1:matches_size]):
                    print(iii)
                    extra_pairs.append([perfect_el[2], element[2], perfect_el[4], element[4], relevance])

            if len(extra_pairs) > 0:
                total_extra_pairs.append(extra_pairs)

    with open(target_output_file, 'w') as csvfile:
        writer = csv.writer(csvfile, delimiter=',', quotechar='|', quoting=csv.QUOTE_MINIMAL)
        writer.writerow(['id', 'question1_id', 'question2_id', 'question1', 'question2', 'relevance'])

        for i, elem in enumerate(np.concatenate(total_extra_pairs)):
            print(i, elem)
            writer.writerow([i, elem[0], elem[1], elem[2], elem[3], elem[4]])
    

In [25]:

generate_extra_question_pairs()

0 Q1 2
0
0
1
1 Q2 2
0
0
1
2 Q3 2
0
0
1
3 Q4 0
4 Q5 1
0
5 Q6 3
0
0
1
1
0
2
6 Q7 0
7 Q8 0
8 Q9 2
0
0
1
9 Q10 2
0
0
1
10 Q11 6
0
0
1
2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
11 Q12 2
0
0
1
12 Q13 0
13 Q14 4
0
0
1
2
1
0
1
2
0
3
14 Q15 0
15 Q16 0
16 Q17 1
0
17 Q18 1
0
18 Q19 0
19 Q20 0
20 Q21 1
0
21 Q22 0
22 Q23 0
23 Q24 0
24 Q25 2
0
0
1
25 Q26 0
26 Q27 4
0
0
1
2
1
0
1
2
0
3
27 Q28 0
28 Q29 1
0
29 Q30 0
30 Q31 0
31 Q32 0
32 Q33 6
0
0
1
2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
33 Q34 1
0
34 Q35 0
35 Q36 2
0
0
1
36 Q37 5
0
0
1
2
3
1
0
1
2
2
0
1
3
0
4
37 Q38 1
0
38 Q39 0
39 Q40 0
40 Q41 3
0
0
1
1
0
2
41 Q42 2
0
0
1
42 Q43 1
0
43 Q44 1
0
44 Q45 0
45 Q46 6
0
0
1
2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
46 Q47 1
0
47 Q48 0
48 Q49 4
0
0
1
2
1
0
1
2
0
3
49 Q50 0
50 Q51 1
0
51 Q52 0
52 Q53 0
53 Q54 0
54 Q55 2
0
0
1
55 Q56 0
56 Q57 1
0
57 Q58 0
58 Q59 3
0
0
1
1
0
2
59 Q60 0
60 Q61 1
0
61 Q62 0
62 Q63 0
63 Q64 0
64 Q65 0
65 Q66 3
0
0
1
1
0
2
66 Q67 5
0
0
1
2
3
1
0
1
2
2
0
1
3
0
4
67 Q68 0
68 Q69 1
0
69 Q70 1
0
70 Q7

207 Q208 7
0
0
1
2
3
4
5
1
0
1
2
3
4
2
0
1
2
3
3
0
1
2
4
0
1
5
0
6
208 Q209 3
0
0
1
1
0
2
209 Q210 2
0
0
1
210 Q211 0
211 Q212 1
0
212 Q213 2
0
0
1
213 Q214 5
0
0
1
2
3
1
0
1
2
2
0
1
3
0
4
214 Q215 5
0
0
1
2
3
1
0
1
2
2
0
1
3
0
4
215 Q216 1
0
216 Q217 0
217 Q218 3
0
0
1
1
0
2
218 Q219 0
219 Q220 2
0
0
1
220 Q221 9
0
0
1
2
3
4
5
6
7
1
0
1
2
3
4
5
6
2
0
1
2
3
4
5
3
0
1
2
3
4
4
0
1
2
3
5
0
1
2
6
0
1
7
0
8
221 Q222 6
0
0
1
2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
222 Q223 2
0
0
1
223 Q224 1
0
224 Q225 1
0
225 Q226 8
0
0
1
2
3
4
5
6
1
0
1
2
3
4
5
2
0
1
2
3
4
3
0
1
2
3
4
0
1
2
5
0
1
6
0
7
226 Q227 2
0
0
1
227 Q228 3
0
0
1
1
0
2
228 Q229 4
0
0
1
2
1
0
1
2
0
3
229 Q230 0
230 Q231 6
0
0
1
2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
231 Q232 4
0
0
1
2
1
0
1
2
0
3
232 Q233 5
0
0
1
2
3
1
0
1
2
2
0
1
3
0
4
233 Q234 6
0
0
1
2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
234 Q235 2
0
0
1
235 Q236 9
0
0
1
2
3
4
5
6
7
1
0
1
2
3
4
5
6
2
0
1
2
3
4
5
3
0
1
2
3
4
4
0
1
2
3
5
0
1
2
6
0
1
7
0
8
236 Q237 1
0
237 Q238 3
0
0
1
1
0
2
2

4
5
6
2
0
1
2
3
4
5
3
0
1
2
3
4
4
0
1
2
3
5
0
1
2
6
0
1
7
0
8
104 Q105 7
0
0
1
2
3
4
5
1
0
1
2
3
4
2
0
1
2
3
3
0
1
2
4
0
1
5
0
6
105 Q106 9
0
0
1
2
3
4
5
6
7
1
0
1
2
3
4
5
6
2
0
1
2
3
4
5
3
0
1
2
3
4
4
0
1
2
3
5
0
1
2
6
0
1
7
0
8
106 Q107 6
0
0
1
2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
107 Q108 5
0
0
1
2
3
1
0
1
2
2
0
1
3
0
4
108 Q109 9
0
0
1
2
3
4
5
6
7
1
0
1
2
3
4
5
6
2
0
1
2
3
4
5
3
0
1
2
3
4
4
0
1
2
3
5
0
1
2
6
0
1
7
0
8
109 Q110 8
0
0
1
2
3
4
5
6
1
0
1
2
3
4
5
2
0
1
2
3
4
3
0
1
2
3
4
0
1
2
5
0
1
6
0
7
110 Q111 8
0
0
1
2
3
4
5
6
1
0
1
2
3
4
5
2
0
1
2
3
4
3
0
1
2
3
4
0
1
2
5
0
1
6
0
7
111 Q112 2
0
0
1
112 Q113 8
0
0
1
2
3
4
5
6
1
0
1
2
3
4
5
2
0
1
2
3
4
3
0
1
2
3
4
0
1
2
5
0
1
6
0
7
113 Q114 10
0
0
1
2
3
4
5
6
7
8
1
0
1
2
3
4
5
6
7
2
0
1
2
3
4
5
6
3
0
1
2
3
4
5
4
0
1
2
3
4
5
0
1
2
3
6
0
1
2
7
0
1
8
0
9
114 Q115 5
0
0
1
2
3
1
0
1
2
2
0
1
3
0
4
115 Q116 6
0
0
1
2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
116 Q117 4
0
0
1
2
1
0
1
2
0
3
117 Q118 9
0
0
1
2
3
4
5
6
7
1
0
1
2
3
4
5
6
2
0
1
2
3
4
5
3
0

2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
266 Q267 0
267 Q268 1
0
268 Q269 6
0
0
1
2
3
4
1
0
1
2
3
2
0
1
2
3
0
1
4
0
5
269 Q270 0
270 Q271 8
0
0
1
2
3
4
5
6
1
0
1
2
3
4
5
2
0
1
2
3
4
3
0
1
2
3
4
0
1
2
5
0
1
6
0
7
271 Q272 1
0
272 Q273 5
0
0
1
2
3
1
0
1
2
2
0
1
3
0
4
273 Q274 4
0
0
1
2
1
0
1
2
0
3
274 Q275 4
0
0
1
2
1
0
1
2
0
3
275 Q276 10
0
0
1
2
3
4
5
6
7
8
1
0
1
2
3
4
5
6
7
2
0
1
2
3
4
5
6
3
0
1
2
3
4
5
4
0
1
2
3
4
5
0
1
2
3
6
0
1
2
7
0
1
8
0
9
276 Q277 4
0
0
1
2
1
0
1
2
0
3
277 Q278 8
0
0
1
2
3
4
5
6
1
0
1
2
3
4
5
2
0
1
2
3
4
3
0
1
2
3
4
0
1
2
5
0
1
6
0
7
278 Q279 4
0
0
1
2
1
0
1
2
0
3
279 Q280 7
0
0
1
2
3
4
5
1
0
1
2
3
4
2
0
1
2
3
3
0
1
2
4
0
1
5
0
6
280 Q281 8
0
0
1
2
3
4
5
6
1
0
1
2
3
4
5
2
0
1
2
3
4
3
0
1
2
3
4
0
1
2
5
0
1
6
0
7
281 Q282 5
0
0
1
2
3
1
0
1
2
2
0
1
3
0
4
282 Q283 7
0
0
1
2
3
4
5
1
0
1
2
3
4
2
0
1
2
3
3
0
1
2
4
0
1
5
0
6
283 Q284 10
0
0
1
2
3
4
5
6
7
8
1
0
1
2
3
4
5
6
7
2
0
1
2
3
4
5
6
3
0
1
2
3
4
5
4
0
1
2
3
4
5
0
1
2
3
6
0
1
2
7
0
1
8
0
9
284 Q285 9
0
0
1
2
3
4
5
6
7
1

479 ['Q34_R46' 'Q34_R55'
 'There are soooooo many ""under the radar"" small businesses here in Qatar; largely (I believe) because the requirements for starting a business are positively daunting to most people. Does Qatar have any thoughts of lowering these hurdles to encourage small businesses to establish and grow in Doha? Are there any legal ways to circumvent the requirements? Thanks; Expat Sueño"'
 'Hi; i took the business visa of my friend in one of the company here in Qatar. but just recently; she said that the need of authenticated letter of sponsor is need in the Philippine Immigration? does anybody know how true is this? Please help...'
 'Relevant']
480 ['Q36_R7' 'Q36_R45'
 'I have heard that it&#39;s really fun to drive from Qatar to Dubai on the weekend (obviosly if you have a 4 X 4 Drive). My question is do I need to get a visa if I want to go to Dubai if I have a Residence Permit of Qatar?'
 'i would like to know whats the procedure to visit dubai and other places from qa

...

5196 ['Q150_R19' 'Q150_R23'
 "I'm from the US; and working in Qatar under my own sponsership. I found out when I was back in the US for the holidays that I'm pregnant. I need to find an OBGYN here in Doha; as I will be here for a while yet. Does anyone know if the hospital will give me problems or refuse to see me because I'm not married? Any advice would be greatly appreciated. Thanks"
 'Hi; Any doctors around working at HMC as resident? I have applied for residency training program at HMC. Awaiting reply; however; I was wondring what would be the salary to expect and allownaces? Do they offer accommodation to married couples? If not what kind of living allowance they give? Basic salary? How is the training there at HMC? Your guidance will be appreciated. Thanks. S.'
 'Irrelevant']
5197 ['Q151_R15' 'Q151_R26'
 'Is there anyway we could get a discount with the speeding ticket; if we pay it through the Traffic Police Offices directly?'
 'I had encountered a traffic fine of qr 6000 for c

5779 ['Q178_R43' 'Q178_R46'
 'I am currently working here in Qatar; our employer informed us that they will transfer to contractor with less salary; but we have option not to accept; but the problem is I have Personal Loan in one of the BAnk here in DOHA; what if I will not accept the offer; what will happen to me ; I mean did the BAnk will force to pay or not?'
 "I'm currently in Doha on a 3 month Visit Visa. Anybody can please tell me; whether I can extend this futher more; maximum of how many months?"
 'Irrelevant']
5780 ['Q178_R43' 'Q178_R50'
 'I am currently working here in Qatar; our employer informed us that they will transfer to contractor with less salary; but we have option not to accept; but the problem is I have Personal Loan in one of the BAnk here in DOHA; what if I will not accept the offer; what will happen to me ; I mean did the BAnk will force to pay or not?'
 'Hi; My husband will start work in Qatar soon and we were wondering how is the work pace there? is it typical

 'Irrelevant']
6213 ['Q203_R37' 'Q203_R49' 'why Arab Girls NOt getting marry indian man'
 'Hi Could you ladies please let me have feed back with regards to your lifestyle and living standrads in Doha. Do you enjoy living there? Whats it like to live there? If you had a choice would you like to be living Qatar; Abu Dhabi or Dubai? My husband has been offered a job in Doha and he is unsure if he should accept. Any help or advice about Doha would be a great help. Thankyou Sandra'
 'Irrelevant']
6214 ['Q203_R39' 'Q203_R43'
 'i am the legal wife here in the philippines.for 4 years;i am hoping that my hubby will get me and my kids there but it will not happen anymore.she has a mistress who resign from hamad sometime in 2005 since she gave birth.He is planning to get her and they will be the legal family in qatar.what will i do?'
 "Can somebody tell me how i get a good job in doha? i have an American passport and holding a husband visas; with a bachelor degree; speaking 3 languages; having a 

 'Irrelevant']
6965 ['Q241_R42' 'Q241_R43'
 'If you were on a plane going the speed of sound and walked from the back of the plane to the front; would you be walking faster than the speed of sound?'
 'I am getting fed up of these spammers with their sales pitches. My question - Does anyone actually visit their site or contact them regarding the items for sale ?'
 'Irrelevant']
6966 ['Q241_R42' 'Q241_R47'
 'If you were on a plane going the speed of sound and walked from the back of the plane to the front; would you be walking faster than the speed of sound?'
 "Can a foreigner obtain a firearm license in Qatar? I know most of you must ask why would I need a license in Qatar; but that's all together a different argument... Please answer only if you have understanding about arms and ammunition law of Qatar."
 'Irrelevant']
6967 ['Q241_R42' 'Q241_R92'
 'If you were on a plane going the speed of sound and walked from the back of the plane to the front; would you be walking faster than the sp

7458 ['Q278_R17' 'Q278_R52'
 'Hi... Hello EveryBody.... can any of you advice me were to go for in weekends in qatar?? actually i am planning to go to Dukan Beach but some guys r telling me to visit Om Said Sea line resort!! i am really confused.... Please can any one of u guide me properly... and how much time does it take to reach both???'
 'any suggestions on what are the happenings in Qatar on Holidays? something new and exciting suggestions please?'
 'Irrelevant']
7459 ['Q278_R28' 'Q278_R34'
 'Hi can anyone tell if its okay to do overnight at umm bab beach? thanks!'
 'http://www.gulf-times.com/site/topics/article.asp?cu_no=2&item_no=251677&version=1&template_id=57&parent_id=56 According to the Gulf Times one of our members at QL; Speed; is a hell of a guy. Read all about him and bow to his engagement. Bravo; Speed.'
 'Irrelevant']
7460 ['Q278_R28' 'Q278_R37'
 'Hi can anyone tell if its okay to do overnight at umm bab beach? thanks!'
 'I know an off-leash area where we could play f

In [72]:
def group_questions_by_org_question(file):
    result = {}
    with open(file, 'r') as csvfile:
        csvreader = csv.reader(csvfile, delimiter=',', quotechar='"')
        next(csvreader, None)

        for row in csvreader:
            if row[1] in result:
                result[row[1]].append(row)
            else:
                result[row[1]] = [row]
    return result
